In [41]:
import numpy as np
import pandas as pd
import os, pickle, sys
from scipy import signal

### input 설정
SRATE = 250 # 250Hz
LEN_INPUT = 20 # input 10s
LEN_PER_NRS = 60 # vital length for each NRS
OVERLAP = 2
n_aug = int((LEN_PER_NRS-LEN_INPUT)/OVERLAP) + 1 # data augmentation 개수




input_path = 'dataset/preprocess2/input3-2/'
if not os.path.exists(input_path[:-1]):
    os.mkdir(input_path[:-1])


if True:
    false_row_list_preop = []
    
    vital_path = '../../cranberry2/Preprocessing/NRS_vital_pickle_unzip/NRS_vital_pickle'
    ecg_path = '../../cranberry2/Preprocessing/ECG_250Hz/ECG_250Hz/ECG,'
    df_preprocess_pacu = pickle.load(open('cache/preprocess2/input3/df_preprocess_pacu','rb'))
    

    ### test set에 해당하는 file_path
    filepath_test = pickle.load(open('filepath_test', 'rb'))
    caseid_test = np.unique(np.array(pd.Series(filepath_test).str.split(',').tolist())[:,2])

    x_train_pacu, y_train_pacu = [], []
    x_test_pacu, y_test_pacu = [], []

    cnt = 0
    for _, row in df_preprocess_pacu.iterrows():
        cnt += 1
        print('loading data {}/{} ...'.format(cnt, len(df_preprocess_pacu)), end='')

        # vital data - PPG (resampling 100 Hz to 250 Hz)
        df_vital = pickle.load(open(vital_path+'/'+row['file_path'], 'rb')).reset_index()
        pleth_samp = df_vital[['Pleth']].fillna(method='ffill', axis=0).fillna(method='bfill', axis=0).values.flatten()
        pleth_resamp = signal.resample(pleth_samp, 120*SRATE)
        ppg_per_NRS = np.full(30000, np.nan)
        ppg_per_NRS[0:len(pleth_resamp)] = pleth_resamp
        

        # vital data - ECG (250Hz)
        ecg_samp = pickle.load(open(ecg_path+row['file_path'][:-3]+'vital', 'rb')).reset_index()[['ECG']]
        ecg_samp = ecg_samp.fillna(method='ffill', axis=0).fillna(method='bfill', axis=0).values.flatten()[0:30000]
        ecg_per_NRS = np.full(30000,np.nan)
        ecg_per_NRS[0:len(ecg_samp)] = ecg_samp
   

        # 한 NRS에 대해 23개의 input 확인
        for i in range(30,51):
            pleth_inp = np.empty
            ecg_inp = np.empty
            # input이 전처리 통과한 경우
            if row[str(i+1)][0]:
                pleth_inp = np.empty
                ecg_inp = np.empty
                
                start_idx = i*OVERLAP*SRATE # 500i
                end_idx = (i*OVERLAP+LEN_INPUT)*SRATE # 500i + 1000


                # input의 normalization
                pleth_inp = ppg_per_NRS[start_idx:end_idx]
                pleth_inp = pleth_inp - np.nanmean(pleth_inp)
                ecg_inp = ecg_per_NRS[start_idx:end_idx]
                ecg_inp = (ecg_inp - np.nanmean(ecg_inp)) / np.nanstd(ecg_inp)
                

                # 해당 caseid가 test set에 속하는 경우
                if row['caseids'] in caseid_test:
                    x_test_pacu.append([pleth_inp, ecg_inp])
                    y_test_pacu.append(int(float(row['NRS'])))

                # 해당 caseid가 train set에 해당하는 경우
                else:
                    x_train_pacu.append([pleth_inp, ecg_inp])
                    y_train_pacu.append(int(float(row['NRS'])))
                #print(fdafsdfas) 
                print(np.nanmean(pleth_inp),np.mean(ecg_inp))

    x_train_pacu = np.array(x_train_pacu, np.float32)
    x_test_pacu = np.array(x_test_pacu, np.float32)
    y_train_pacu = np.array(y_train_pacu, int)
    y_test_pacu = np.array(y_test_pacu, int)


    
    
    
print('size of training set(pacu):', len(x_train_pacu))
print('size of test set(pacu):', len(x_test_pacu))

loading data 1/8294 ...5.729816621169448e-15 5.684341886080802e-18
3.637978807091713e-15 0.0
-1.8189894035458566e-16 -1.7053025658242403e-17
-9.094947017729283e-16 -2.2737367544323207e-17
4.18367562815547e-15 -3.4106051316484806e-17
1.2732925824820995e-15 2.842170943040401e-17
-1.6370904631912708e-15 1.7053025658242403e-17
2.0008883439004422e-15 0.0
3.637978807091713e-16 -6.821210263296961e-17
2.9103830456733705e-15 1.1368683772161604e-17
3.4560798667371273e-15 4.5474735088646414e-17
4.5474735088646414e-17 2.2737367544323207e-17
2.9558577807620166e-16 1.1368683772161604e-17
-4.934008757118136e-15 2.9842794901924206e-17
3.4560798667371273e-15 0.0
4.320099833421409e-16 2.1316282072803006e-17
-8.86757334228605e-16 -1.1368683772161604e-17
-8.640199666842818e-16 0.0
loading data 2/8294 ...loading data 3/8294 ...-4.092726157978177e-16 1.7053025658242403e-17
2.319211489520967e-15 -1.1368683772161604e-17
1.7053025658242404e-15 -5.684341886080802e-18
2.546585164964199e-15 -1.9895196601282805e-1

loading data 20/8294 ...-3.069544618483633e-16 7.531752999057062e-17
1.8417267710901796e-15 -6.821210263296961e-17
3.9392489270539955e-15 0.0
2.2509993868879976e-15 4.5474735088646414e-17
2.228262019343674e-15 -3.836930773104541e-17
-1.6825651982799173e-15 6.465938895416912e-17
5.229594535194337e-16 -3.4106051316484806e-17
3.797140379901975e-15 -5.684341886080802e-18
-9.890754881780594e-15 -1.1368683772161604e-17
8.526512829121202e-16 6.3948846218409015e-18
2.2737367544323207e-17 1.1368683772161604e-17
-2.756905814749189e-15 3.126388037344441e-17
6.940581442904659e-15 3.268496584496461e-17
5.468336894409731e-15 -6.536993168992922e-17
1.1198153515579178e-15 1.2789769243681803e-17
4.7407411329913885e-15 -1.9184653865522706e-17
2.540900823078118e-15 -2.9842794901924206e-17
-2.5011104298755525e-15 -3.694822225952521e-17
2.813749233609997e-15 1.5631940186722205e-17
-1.48929757415317e-15 -5.684341886080802e-18
-1.6143530956469477e-15 3.268496584496461e-17
loading data 21/8294 ...-7.275957614

-3.54702933691442e-15 -3.339550858072471e-17
3.819877747446298e-15 -3.268496584496461e-17
1.909938873723149e-15 -1.8474111129762604e-17
4.229150363244116e-15 1.5631940186722205e-17
-5.911715561524033e-16 -3.979039320256561e-17
1.3869794202037157e-15 2.4868995751603507e-17
-2.5920599000528456e-15 -1.9895196601282805e-17
-1.2732925824820995e-15 -2.5579538487363606e-17
-8.185452315956354e-16 5.684341886080802e-18
-2.3646862246096133e-15 1.4210854715202004e-17
2.2737367544323207e-17 -4.263256414560601e-17
4.320099833421409e-16 1.0658141036401503e-17
-4.274625098332763e-15 -1.4210854715202004e-17
-2.9558577807620166e-15 5.4711790653527716e-17
loading data 41/8294 ...8.412825991399587e-16 -2.7000623958883807e-17
-5.070432962384075e-15 -2.842170943040401e-18
5.638867150992155e-15 -2.7711166694643906e-17
1.0004441719502211e-15 -4.831690603168681e-17
-9.549694368615746e-16 1.2079226507921702e-17
4.6838977141305805e-15 -2.9842794901924206e-17
-2.2509993868879976e-15 3.979039320256561e-17
3.22870

-1.8189894035458565e-15 -2.9842794901924206e-17
6.8666849983856085e-15 -9.237055564881302e-18
-4.18367562815547e-15 -4.405364961712621e-17
2.8990143619012086e-15 -2.1316282072803004e-18
-3.728928277269006e-15 -1.6342482922482304e-17
5.002220859751106e-16 -2.842170943040401e-18
-3.4788172342814504e-15 -2.842170943040401e-18
-1.2278178473934532e-15 4.405364961712621e-17
loading data 59/8294 ...1.6825651982799173e-15 3.4106051316484806e-17
-2.5011104298755525e-15 1.9895196601282805e-17
-2.091837814077735e-15 5.684341886080802e-17
loading data 60/8294 ...1.4551915228366853e-15 2.842170943040401e-18
5.820766091346741e-15 -1.1368683772161604e-17
3.637978807091713e-16 3.4106051316484806e-17
-3.637978807091713e-16 0.0
-1.8189894035458565e-15 -5.684341886080802e-18
3.637978807091713e-15 -2.842170943040401e-17
-2.7284841053187845e-16 -1.7053025658242403e-17
-5.638867150992155e-15 -8.526512829121201e-18
4.638422979041934e-15 5.684341886080802e-18
2.319211489520967e-15 5.684341886080802e-18
7.2759

loading data 77/8294 ...-1.4551915228366853e-15 -2.2026824808563105e-17
loading data 78/8294 ...-5.093170329928398e-15 5.684341886080802e-18
-4.729372449219227e-15 1.4210854715202004e-17
-1.0913936421275138e-15 2.5579538487363606e-17
0.0 -1.2789769243681803e-17
-1.3642420526593924e-15 2.842170943040401e-18
-6.434675015043467e-15 3.4106051316484806e-17
2.319211489520967e-15 1.7053025658242403e-17
1.1823431123048067e-15 5.684341886080802e-18
5.002220859751105e-15 1.7053025658242403e-17
-1.8189894035458566e-16 -2.2737367544323207e-17
1.546140993013978e-15 0.0
-1.0913936421275138e-15 2.2737367544323207e-17
5.911715561524033e-16 0.0
2.3646862246096133e-15 -2.2737367544323207e-17
7.73070496506989e-16 2.5579538487363606e-17
-3.1377567211166024e-15 2.842170943040401e-17
-6.184563972055912e-15 -3.4106051316484806e-17
-7.275957614183426e-16 3.4106051316484806e-17
-2.7739588404074313e-15 0.0
-5.002220859751105e-15 -2.2737367544323207e-17
-9.094947017729283e-16 -2.2737367544323207e-17
loading data

...

loading data 8228/8294 ...loading data 8229/8294 ...loading data 8230/8294 ...4.911271389573813e-15 -3.694822225952521e-17
3.3651303965598346e-15 2.2737367544323207e-17
3.4560798667371273e-15 -5.684341886080802e-18
-1.2732925824820995e-15 1.1368683772161604e-17
-9.094947017729283e-16 -2.842170943040401e-17
2.2737367544323206e-15 -1.8474111129762604e-17
2.2737367544323206e-16 3.126388037344441e-17
-3.637978807091713e-16 -1.8474111129762604e-17
3.9108272176235914e-15 -4.263256414560601e-17
-6.0936145018786194e-15 1.7053025658242403e-17
1.8189894035458566e-16 -2.4158453015843405e-17
-3.637978807091713e-16 2.842170943040401e-18
-9.094947017729283e-17 -2.9842794901924206e-17
-1.8189894035458565e-15 5.968558980384841e-17
-5.638867150992155e-15 8.526512829121201e-18
-2.2737367544323206e-15 2.842170943040401e-17
loading data 8231/8294 ...-9.094947017729283e-16 3.126388037344441e-17
1.7280399333685636e-15 -2.7711166694643906e-17
4.729372449219227e-15 -4.263256414560601e-17
-1.0004441719502211e-

loading data 8244/8294 ...loading data 8245/8294 ...-3.774403012357652e-15 9.368505970996921e-14
-1.9554136088117957e-15 2.345785787838395e-13
5.297806637827307e-15 -4.182176382983016e-13
3.001332515850663e-15 9.417817636858672e-14
-3.069544618483633e-16 7.105427357601002e-18
-1.0004441719502211e-15 3.7720724321843593e-13
4.092726157978177e-16 4.2138168510064135e-13
-3.54702933691442e-15 -3.7753977721877164e-13
-3.183231456205249e-15 -5.051944640399597e-13
-4.320099833421409e-15 -5.109342282594298e-13
-5.775291356258094e-15 -4.1642920223239343e-13
5.525180313270539e-15 -2.797378328978084e-13
-3.001332515850663e-15 3.24133964113571e-13
4.774847184307873e-16 -4.16750367548957e-13
4.797584551852197e-15 1.4084662325331009e-13
1.5006662579253316e-15 -2.340669880140922e-13
-2.842170943040401e-15 1.4078693766350625e-13
2.0463630789890884e-15 2.8195188406243685e-13
2.660272002685815e-15 -4.602043190971017e-14
8.185452315956354e-15 1.363787305308506e-13
6.8666849983856085e-15 -7.105427357601002

-3.865352482534945e-15 -5.684341886080802e-17
1.6143530956469477e-15 0.0
2.0008883439004422e-15 4.5474735088646414e-17
-2.9331204132176936e-15 4.5474735088646414e-17
-1.77351466845721e-15 2.2737367544323207e-17
3.774403012357652e-15 0.0
loading data 8261/8294 ...-5.229594535194337e-16 3.694822225952521e-17
-3.9790393202565614e-15 -1.3500311979441904e-17
-3.410605131648481e-16 5.1869619710487314e-17
-7.571543392259628e-15 -8.171241461241152e-18
-6.662048690486699e-15 -5.684341886080802e-18
4.6156856114976105e-15 -5.684341886080802e-18
1.602984411874786e-15 5.115907697472721e-17
-2.432898327242583e-15 -1.7763568394002505e-17
2.2509993868879976e-15 -1.9895196601282805e-17
1.0913936421275138e-15 1.8474111129762604e-17
3.819877747446298e-15 -4.121147867408581e-17
8.640199666842818e-16 5.684341886080802e-18
2.091837814077735e-15 -3.126388037344441e-17
4.138200893066824e-15 -1.7053025658242403e-17
-2.5579538487363606e-15 -4.405364961712621e-17
-2.7398527890909463e-15 5.684341886080802e-17
3.2

loading data 8280/8294 ...-7.639755494892597e-15 -2.2737367544323207e-17
2.1827872842550276e-15 -5.684341886080802e-18
-2.9103830456733705e-15 -2.5579538487363606e-17
-2.546585164964199e-15 -1.9895196601282805e-17
-3.001332515850663e-15 4.121147867408581e-17
-5.820766091346741e-15 -2.9842794901924206e-17
-2.1827872842550276e-15 1.4210854715202004e-17
2.5011104298755525e-15 -7.105427357601002e-18
1.2278178473934532e-15 3.694822225952521e-17
3.3651303965598346e-15 1.1368683772161604e-17
7.275957614183426e-16 0.0
loading data 8281/8294 ...-2.9558577807620166e-15 1.1368683772161604e-17
-5.4569682106375695e-15 5.684341886080802e-18
4.82032191939652e-15 2.842170943040401e-18
loading data 8282/8294 ...2.546585164964199e-15 -2.1859136722923722e-14
8.549250196665526e-15 6.237996785785071e-14
9.549694368615746e-16 5.553886239795247e-14
-1.0913936421275138e-15 3.973781304011936e-14
-1.8189894035458566e-16 -5.546496595343342e-14
-5.229594535194337e-15 7.933067536214366e-14
9.094947017729283e-17 -1

size of training set(pacu): 103765
size of test set(pacu): 10965


In [23]:
a=x_train_pacu[1][0]
print(np.nanmean(a))

2.4414062e-08


In [ ]:
input_path = 'dataset/preprocess2/input3-2/'

# loading pacu
print('loading pacu data...', flush=True, end='')
x_train_pacu = np.load(input_path+'x_train_pacu.npz', allow_pickle=True)['arr_0']
y_train_pacu = np.load(input_path+'y_train_pacu.npz')['arr_0']
x_test_pacu = np.load(input_path+'x_test_pacu.npz', allow_pickle=True)['arr_0']
y_test_pacu = np.load(input_path+'y_test_pacu.npz')['arr_0']
print('done', flush=True)

print('x_train_pacu shape:', x_train_pacu.shape)
print('x_test_pacu shape:', x_test_pacu.shape)

# loading preop
print('loading preop data...', flush=True, end='')
x_train_preop = np.load(input_path+'x_train_preop.npz', allow_pickle=True)['arr_0']
y_train_preop = np.load(input_path+'y_train_preop.npz')['arr_0']
x_test_preop = np.load(input_path+'x_test_preop.npz', allow_pickle=True)['arr_0']
y_test_preop = np.load(input_path+'y_test_preop.npz')['arr_0']
print('done', flush=True)

print('x_train_preop shape:', x_train_preop.shape)
print('x_test_preop shape:', x_test_preop.shape)


# PACU와 preop 데이터 합치기
x_train = np.concatenate((x_train_pacu, x_train_preop), axis = 0)
y_train = np.concatenate((y_train_pacu, y_train_preop), axis = 0)
x_test = np.concatenate((x_test_pacu, x_test_preop), axis = 0)
y_test = np.concatenate((y_test_pacu, y_test_preop), axis = 0)


# 알맞게 input 변환
x_train = np.transpose(x_train, [0,2,1])
x_test = np.transpose(x_test, [0,2,1])

print('x_train shape:', x_train.shape)
print('x_test shape:', x_test.shape)


# filling nan
x_train[:,:,0] = pd.DataFrame(x_train[:,:,0]).fillna(method='ffill', axis=1).fillna(method='bfill', axis=1).values
x_train[:,:,1] = pd.DataFrame(x_train[:,:,1]).fillna(method='ffill', axis=1).fillna(method='bfill', axis=1).values
x_test[:,:,0] = pd.DataFrame(x_test[:,:,0]).fillna(method='ffill', axis=1).fillna(method='bfill', axis=1).values
x_test[:,:,1] = pd.DataFrame(x_test[:,:,1]).fillna(method='ffill', axis=1).fillna(method='bfill', axis=1).values

y_train_bin = y_train>=5
print('train {} ({} events {:.1f}%), test {}'.format(len(y_train_bin), sum(y_train_bin), 100*np.mean(y_train_bin), len(x_test)))


# 저장하기 - completed train, test set
print('saving...', end='', flush=True)
np.savez_compressed(input_path+'x_train.npz', x_train)
np.savez_compressed(input_path+'x_test.npz', x_test)
np.savez_compressed(input_path+'y_train.npz', y_train)
np.savez_compressed(input_path+'y_test.npz', y_test)
print('done', flush=True)